In [ ]:
import numpy as np
import netCDF4 as nc
import matplotlib.pyplot as plt
import cartopy.crs as ccrs

In [ ]:
path_to_data = 'XX'
TS_data = nc.Dataset(path_to_data)['XX']
lon = nc.Dataset(path_to_data)['XX']
lat = nc.Dataset(path_to_data)['XX']

path_to_areacella = 'XX'
areacella = nc.Dataset(path_to_areacella)['XX']

path_to_landmask = 'XX'
landmask = nc.Dataset(path_to_landmask)['XX'][:]

### Making a timeseries

In [ ]:
## what is the shape of ts?
TS_data

In [ ]:
print(np.shape(TS_data)), print(np.shape(lon)), print(np.shape(lat));

The shape of TS is (time, lat, lon).

#### Make a timeseries of the surface temperature at 10N, 30 E

In [ ]:
ind_lon = np.where(lon[:] >= XX)[0][0] # find where lon is about 30
print(ind_lon)

In [ ]:
ind_lat = np.where(lat[:] >= XX)[0][0] # find where lon is about 30
print(ind_lat)

In [ ]:
## define time axis
time = np.linspace(0, len(TS_data)/12, len(TS_data))

In [ ]:
plt.figure(dpi=120)
plt.plot(time,TS_data[:, ind_lat, ind_lon])
plt.ylabel('Surface Temperature (K)')
plt.xlabel('Time (years)')
plt.xlim(0,20)

### Spatial Averaging

#### Plot GMST vs. time

In [ ]:
GMST = np.sum(np.sum(XX, axis = -1), axis=-1)/np.sum(XX)

Plot a timeseries of GMST using the weighted mean and a non-weighted mean. Why is a weighted mean necessary? Explain the difference in the timeseries between the weighted and non-weighted mean.

In [ ]:
plt.figure(dpi=120)
plt.plot(time,XX, label = 'Weighted Mean')
plt.plot(time, XX, label = 'Mean')
plt.ylabel('GMST (K)')
plt.xlabel('Time (years)')
plt.xlim(0,20)
plt.legend()

#### Why is there a seasonal cycle in GMST?

### Calculating Composites

Composites are useful when analyzing specific events, say El Nino.

In this example, we will make composites of Northern Hemisphere winter (DJF) and calculate the composite mean.

In [ ]:
DJF_TS_data = [np.mean(TS_data[i*12-XX:i*12+XX],axis=0) for i in range(1,int(len(TS_data)/12))]
JJA_TS_data = [np.mean(TS_data[i*12+XX:i*12+XX],axis=0) for i in range(1,int(len(TS_data)/12))]

In [ ]:
plt.figure(figsize=(8, 5))
plt.imshow(DJF_TS_data[0], vmin=240,vmax=320,cmap="coolwarm", origin="lower")
plt.colorbar(label="DJF Year 1 (K)")
plt.xlabel("Longitude")
plt.ylabel("Latitude")
plt.title("DJF Surface Temperature Year 1")
plt.show()

In [ ]:
plt.figure(figsize=(8, 5))
plt.imshow(JJA_TS_data[0], vmin=240,vmax=320,cmap="coolwarm", origin="lower")
plt.colorbar(label="JJA Year 1 (K)")
plt.xlabel("Longitude")
plt.ylabel("Latitude")
plt.title("JJA Surface Temperature Year 1")
plt.show()

In [ ]:
## composite means
comp_mean_DJF_TS = XX
comp_mean_JJA_TS = XX

fig, ax = plt.subplots(1,3,figsize=(20,10), tight_layout=True)

c= ax[0].imshow(XX, vmin=240,vmax=320,cmap="coolwarm", origin="lower")
plt.colorbar(c, label="DJF Mean(K)", ax=ax[0], shrink=0.3)
ax[0].set_xlabel("Longitude")
ax[0].set_ylabel("Latitude")
ax[0].set_title('DJF Composite Mean (K)')

c= ax[1].imshow(XX, vmin=240,vmax=320,cmap="coolwarm", origin="lower")
plt.colorbar(c, label="JJA Mean (K)", ax=ax[1],shrink=0.3)
ax[1].set_xlabel("Longitude")
ax[1].set_ylabel("Latitude")
ax[1].set_title('JJA Composite Mean (K)')

c= ax[2].imshow(XX, vmin=-50,vmax=50,cmap="bwr", origin="lower")
plt.colorbar(c, label="DJF-JJA Mean (K)", ax=ax[2],shrink=0.3)
ax[2].set_xlabel("Longitude")
ax[2].set_ylabel("Latitude")
ax[2].set_title('DJF - JJA Composite Mean (K)')

### Performing PCA

PCA requires making a covariance matrix, which is often slow for big datasets. Instead we will do SVD (Singular Value Decomposition).

#### Step one: remove the local time mean from the data and only take SST (where landmask=0)

In [ ]:
oceanmask = landmask*0
oceanmask[XX] = 1 # set ocean mask to one where landmask==0

In [ ]:
## calculate time mean at each lat-lon point

TS_mean = np.mean(XX) # take mean over time axis only over ocean

In [ ]:
TS_anom = XX # remove mean 

In [ ]:
TS_anom_2d = XX # reshape anomaly to have shape (time, latxlon)

In [ ]:
U, S, Vt = np.linalg.svd(XX, full_matrices=False) # perform SVD on 2d dataset

In [ ]:
print(XX) # print the shape of each matrix

In [ ]:
eigenvalues = XX  # Convert singular values to eigenvalues
eigenvectors = XX  # Principal components

In [ ]:
plt.figure(dpi=120)
plt.plot(XX,'k.')
plt.ylabel('Fraction of Variance Explained by Each PC')
plt.xlabel('PC')

plt.xlim(-1,40)
plt.yscale('log')
plt.ylim(1e-4,2)

In [ ]:
# Extract PC1 time series (scaled)
pc1_time_series = U[:, 0] * S[0]  # PC1 time series 

# Get PC1 spatial pattern 
pc1_spatial_pattern = eigenvectors[:,0].reshape(len(lat),len(lon))  # put back in lat-lon shape

# Scale PC1 anomalies back to temperature-like values (time, lat, lon)
pc1_anomalies = pc1_time_series[:, np.newaxis, np.newaxis] * pc1_spatial_pattern

# Visualize an example frame (e.g., first time step)
plt.figure(figsize=(8, 5))
plt.imshow(pc1_anomalies[0], vmin=-10,vmax=10,cmap="coolwarm", origin="lower")
plt.colorbar(label="Temperature Anomaly (K or °C)")
plt.xlabel("Longitude Index")
plt.ylabel("Latitude Index")
plt.title("PC1 Temperature Anomaly for First Time Step")
plt.show()


In [ ]:
time = np.linspace(0, len(pc1_time_series)/12, len(pc1_time_series))
plt.figure(dpi=120)
plt.plot(time,pc1_time_series)
plt.xlim(0,5)

What signal does this look like? Repeat this for the next two PCs. Where do you see a signal that may be El Nino?